In [ ]:
pip install tensorflow

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 590.6/590.6 MB 1.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 59.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 kB 6.9 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 59.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.1/5.1 MB 64.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 133.7/133.7 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 65.5/65.5 kB 7.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.5/24.5 MB 39.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.3/80.3 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 60.7 MB/s eta 0:0

In [ ]:
pip install -q mlflow

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [ ]:
spark.conf.set("fs.azure.account.key.databjune.dfs.core.windows.net","Enter Account key to connect to ADLS Storage Account")

In [ ]:
cust_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/customer.csv",header=True,inferSchema=True)
)
add_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/address.csv",header=True,inferSchema=True)
)
dem_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/demographic.csv",header=True,inferSchema=True)
)
term_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/termination.csv",header=True,inferSchema=True)
)

In [ ]:
# Additional Datasets

unemp_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/TXUR.csv",header=True,inferSchema=True)
)
mhi_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/MEHOINUSTXA672N.csv",header=True,inferSchema=True)
)

pci_df = (spark.read
  .format("csv")
  .option("mode", "PERMISSIVE")
  .load("abfss://bronze@databjune.dfs.core.windows.net/TXPCPI.csv",header=True,inferSchema=True)
)

In [ ]:
cust_df_sub= cust_df.select("INDIVIDUAL_ID", "ADDRESS_ID","CURR_ANN_AMT","DAYS_TENURE","CUST_ORIG_DATE","AGE_IN_YEARS","DATE_OF_BIRTH")

add_df_sub= add_df.select("ADDRESS_ID","LATITUDE","LONGITUDE","COUNTY")

dem_df_sub= dem_df.select("INDIVIDUAL_ID", "INCOME","HAS_CHILDREN","LENGTH_OF_RESIDENCE","MARITAL_STATUS","HOME_MARKET_VALUE","HOME_OWNER","COLLEGE_DEGREE")

In [ ]:
from pyspark.sql.functions import col, when
#Add Churn Column

term_df = term_df.withColumn("Churn", when(col("ACCT_SUSPD_DATE").isNotNull(), 1).otherwise(0))


In [ ]:
add_df_sub = add_df.withColumn(
    "County_enc",
    when(col("County") == "Dallas", 1)
    .when(col("County") == "Tarrant", 2)
    .otherwise(3)
)

# Show the DataFrame
add_df.show()

+----------------+------------------+----------+--------------------+-----------+-----+--------+
|      ADDRESS_ID|          LATITUDE| LONGITUDE|      STREET_ADDRESS|       CITY|STATE|  COUNTY|
+----------------+------------------+----------+--------------------+-----------+-----+--------+
|5.21301086809E11|         32.315803|-96.627896|8457 Wright Mount...|      Ennis|   TX|   Ellis|
|5.21300039185E11|              NULL|      NULL|082 Cline Mountai...|     Irving|   TX|  Dallas|
|5.21300239034E11|          32.80629|-96.779857|      457 John Mills|     Dallas|   TX|  Dallas|
|5.21301307921E11|         32.825737|-96.939687| 5726 Barnett Meadow|     Irving|   TX|  Dallas|
|5.21300970034E11|         32.867192|-96.715552|  050 Nicholas Views|     Dallas|   TX|  Dallas|
|5.21301487164E11|         33.055527|-96.705288|   207 Rebecca Brook|      Plano|   TX|  Collin|
|5.21300610942E11|         33.406005|-96.966034|  9983 Jesse Landing|Pilot Point|   TX|  Denton|
|5.21300852902E11|         32.

In [ ]:
merged_df = cust_df_sub.join(add_df_sub, "ADDRESS_ID", "inner")

m1_df=merged_df.join(dem_df_sub,"INDIVIDUAL_ID","inner")

m2_df=m1_df.join(term_df,"INDIVIDUAL_ID")

In [ ]:
m2_df=m2_df.select("CURR_ANN_AMT","DAYS_TENURE","AGE_IN_YEARS","LATITUDE","LONGITUDE","County_enc","INCOME","HAS_CHILDREN","LENGTH_OF_RESIDENCE","MARITAL_STATUS","HOME_MARKET_VALUE","HOME_OWNER","COLLEGE_DEGREE","Churn")

In [ ]:
m2_df.schema

StructType([StructField('CURR_ANN_AMT', DoubleType(), True), StructField('DAYS_TENURE', DoubleType(), True), StructField('AGE_IN_YEARS', DoubleType(), True), StructField('LATITUDE', DoubleType(), True), StructField('LONGITUDE', DoubleType(), True), StructField('County_enc', IntegerType(), False), StructField('INCOME', DoubleType(), True), StructField('HAS_CHILDREN', DoubleType(), True), StructField('LENGTH_OF_RESIDENCE', DoubleType(), True), StructField('MARITAL_STATUS', StringType(), True), StructField('HOME_MARKET_VALUE', StringType(), True), StructField('HOME_OWNER', IntegerType(), True), StructField('COLLEGE_DEGREE', IntegerType(), True), StructField('Churn', IntegerType(), False)])

In [ ]:
display(m2_df)


CURR_ANN_AMT DAYS_TENURE AGE_IN_YEARS LATITUDE LONGITUDE County_enc INCOME HAS_CHILDREN LENGTH_OF_RESIDENCE MARITAL_STATUS HOME_MARKET_VALUE HOME_OWNER COLLEGE_DEGREE Churn 1373.99268 1933.0 53.221 33.034213 -96.819046 3 125000.0 1.0 7.0 Married 400000 - 449999 1 0 1 1060.836619 192.0 70.639 32.933442 -96.36667 3 62500.0 1.0 4.0 Married 75000 - 99999 1 0 1 997.302624 3508.0 65.969 32.720126 -96.662478 1 27500.0 1.0 5.0 Single 50000 - 74999 1 1 1 885.500714 238.0 50.557 32.71516200000001 -96.880735 1 22500.0 1.0 8.0 Married 100000 - 124999 0 0 1 1429.717555 159.0 61.558 33.02103 -97.090345 3 125000.0 1.0 5.0 Married 125000 - 149999 1 1 1 1204.370556 1237.0 51.806 32.876997 -97.21946 2 87500.0 0.0 6.0 Single 75000 - 99999 1 0 1 616.119659 443.0 30.053 null null 1 5000.0 1.0 3.0 Married 100000 - 124999 0 1 1 983.041308 6291.0 66.639 32.841451 -96.797974 1 250000.0 0.0 15.0 Married 300000 - 349999 1 1 1 679.392374 3031.0 41.64 32.801311 -97.452319 2 22500.0 0.0 14.0 Single 50000 - 74999 1 0 1 963.840369 80.0 55.444 null null 2 80372.176 0.0 0.0 null null 0 0 1 1567.365829 2532.0 29.473 32.868379 -96.600493 1 125000.0 1.0 6.0 Married 125000 - 149999 1 0 1 1171.284466 2996.0 72.641 32.843248 -97.113303 2 80372.176 0.0 15.0 Single 125000 - 149999 1 0 1 546.678742 96.0 44.222 null null 1 57500.0 1.0 0.0 Single 25000 - 49999 1 0 1 981.445434 168.0 40.893 33.190909 -96.529343 3 80372.176 0.0 6.801 null 175000 - 199999 0 0 1 945.297622 4937.0 47.97 null null 1 42500.0 1.0 6.801 null 225000 - 249999 0 0 1 1237.00314 293.0 58.053 32.819837 -97.278905 2 47500.0 0.0 8.0 Single 50000 - 74999 0 0 1 924.391668 286.0 57.054 32.795447 -97.294992 2 12500.0 1.0 3.0 Single 50000 - 74999 1 0 1 867.214433 803.0 55.444 null null 3 87500.0 0.0 0.0 null null 0 0 1 977.064441 80.0 55.444 32.744792 -97.49844 2 80372.176 0.0 6.801 null 50000 - 74999 0 0 1 635.944122 1204.0 55.444 32.90597 -96.859524 1 37500.0 0.0 1.0 null 250000 - 274999 0 0 1 1297.781473 119.0 50.472 32.918775 -97.277929 2 87500.0 1.0 3.0 Married 225000 - 249999 1 0 1 898.380862 2008.0 55.444 null null 2 47500.0 0.0 0.0 null null 0 0 1 920.568262 6291.0 45.388 33.093250000000005 -96.752359 3 87500.0 0.0 1.0 Single 100000 - 124999 1 0 1 1069.87835 5095.0 39.387 32.602403 -96.7635 1 47500.0 1.0 2.0 Single 100000 - 124999 1 0 1 979.453125 1616.0 40.055 32.783301 -97.387241 2 32500.0 1.0 4.0 Single 75000 - 99999 1 1 1 664.00246 3614.0 55.444 32.649946 -96.846601 1 80372.176 0.0 1.0 null 75000 - 99999 0 0 1 1359.389277 163.0 40.222 32.950871 -96.683221 1 87500.0 1.0 15.0 Married 100000 - 124999 1 0 1 571.231533 235.0 82.387 33.143345 -96.770178 3 70000.0 0.0 6.0 Married 175000 - 199999 1 1 1 1439.698393 5332.0 44.474 33.180583 -96.917024 3 87500.0 1.0 9.0 Married 100000 - 124999 1 1 1 705.461263 5095.0 39.387 null null 3 47500.0 1.0 2.0 Married 175000 - 199999 0 0 1 1239.998157 106.0 47.053 32.948199 -96.723273 1 62500.0 0.0 12.0 Single 1000 - 24999 1 0 1 343.993275 5230.0 89.558 32.672206 -97.158259 2 70000.0 0.0 15.0 Married 75000 - 99999 1 0 1 1225.955771 4308.0 44.14 32.999225 -97.068418 3 250000.0 0.0 8.0 Married 150000 - 174999 1 1 1 846.935188 3922.0 60.893 32.849723999999995 -96.96622 1 125000.0 0.0 15.0 Single 150000 - 174999 1 0 1 1201.134006 80.0 55.444 null null 1 12500.0 0.0 0.0 null null 0 0 1 1042.806697 129.0 53.306 32.66534 -96.916357 1 87500.0 1.0 5.0 Married 125000 - 149999 1 0 1 1061.290149 6291.0 58.387 32.333374 -96.66509 3 87500.0 1.0 2.0 Married 125000 - 149999 1 0 1 964.828338 116.0 33.807 33.171758 -96.698662 3 87500.0 0.0 4.0 Single 100000 - 124999 1 0 1 1134.149279 80.0 39.89 null null 3 87500.0 1.0 0.0 Married null 0 1 1 881.815219 337.0 64.14 32.849107 -97.388363 2 125000.0 0.0 10.0 Married 75000 - 99999 1 1 1 777.013338 118.0 50.305 32.643711 -97.026669 1 57500.0 0.0 1.0 Married 25000 - 49999 1 0 1 824.728469 198.0 72.055 32.704478 -97.316443 2 22500.0 0.0 5.0 Married 25000 - 49999 1 0 1 819.223899 80.0 55.444 32.613659 -96.776224 1 80372.176 0.0 6.801 null 75000 

In [ ]:
from pyspark.sql.functions import col, when

m2_df = m2_df.withColumn(
    "MARITAL_STATUS_Enc",
    when(col("MARITAL_STATUS") == "Single", 1)
    .when(col("MARITAL_STATUS") == "Married", 2)
    .otherwise(3)
)

display(m2_df)

CURR_ANN_AMT DAYS_TENURE AGE_IN_YEARS LATITUDE LONGITUDE County_enc INCOME HAS_CHILDREN LENGTH_OF_RESIDENCE MARITAL_STATUS HOME_MARKET_VALUE HOME_OWNER COLLEGE_DEGREE Churn MARITAL_STATUS_Enc 1373.99268 1933.0 53.221 33.034213 -96.819046 3 125000.0 1.0 7.0 Married 400000 - 449999 1 0 1 2 1060.836619 192.0 70.639 32.933442 -96.36667 3 62500.0 1.0 4.0 Married 75000 - 99999 1 0 1 2 997.302624 3508.0 65.969 32.720126 -96.662478 1 27500.0 1.0 5.0 Single 50000 - 74999 1 1 1 1 885.500714 238.0 50.557 32.71516200000001 -96.880735 1 22500.0 1.0 8.0 Married 100000 - 124999 0 0 1 2 1429.717555 159.0 61.558 33.02103 -97.090345 3 125000.0 1.0 5.0 Married 125000 - 149999 1 1 1 2 1204.370556 1237.0 51.806 32.876997 -97.21946 2 87500.0 0.0 6.0 Single 75000 - 99999 1 0 1 1 616.119659 443.0 30.053 null null 1 5000.0 1.0 3.0 Married 100000 - 124999 0 1 1 2 983.041308 6291.0 66.639 32.841451 -96.797974 1 250000.0 0.0 15.0 Married 300000 - 349999 1 1 1 2 679.392374 3031.0 41.64 32.801311 -97.452319 2 22500.0 0.0 14.0 Single 50000 - 74999 1 0 1 1 963.840369 80.0 55.444 null null 2 80372.176 0.0 0.0 null null 0 0 1 3 1567.365829 2532.0 29.473 32.868379 -96.600493 1 125000.0 1.0 6.0 Married 125000 - 149999 1 0 1 2 1171.284466 2996.0 72.641 32.843248 -97.113303 2 80372.176 0.0 15.0 Single 125000 - 149999 1 0 1 1 546.678742 96.0 44.222 null null 1 57500.0 1.0 0.0 Single 25000 - 49999 1 0 1 1 981.445434 168.0 40.893 33.190909 -96.529343 3 80372.176 0.0 6.801 null 175000 - 199999 0 0 1 3 945.297622 4937.0 47.97 null null 1 42500.0 1.0 6.801 null 225000 - 249999 0 0 1 3 1237.00314 293.0 58.053 32.819837 -97.278905 2 47500.0 0.0 8.0 Single 50000 - 74999 0 0 1 1 924.391668 286.0 57.054 32.795447 -97.294992 2 12500.0 1.0 3.0 Single 50000 - 74999 1 0 1 1 867.214433 803.0 55.444 null null 3 87500.0 0.0 0.0 null null 0 0 1 3 977.064441 80.0 55.444 32.744792 -97.49844 2 80372.176 0.0 6.801 null 50000 - 74999 0 0 1 3 635.944122 1204.0 55.444 32.90597 -96.859524 1 37500.0 0.0 1.0 null 250000 - 274999 0 0 1 3 1297.781473 119.0 50.472 32.918775 -97.277929 2 87500.0 1.0 3.0 Married 225000 - 249999 1 0 1 2 898.380862 2008.0 55.444 null null 2 47500.0 0.0 0.0 null null 0 0 1 3 920.568262 6291.0 45.388 33.093250000000005 -96.752359 3 87500.0 0.0 1.0 Single 100000 - 124999 1 0 1 1 1069.87835 5095.0 39.387 32.602403 -96.7635 1 47500.0 1.0 2.0 Single 100000 - 124999 1 0 1 1 979.453125 1616.0 40.055 32.783301 -97.387241 2 32500.0 1.0 4.0 Single 75000 - 99999 1 1 1 1 664.00246 3614.0 55.444 32.649946 -96.846601 1 80372.176 0.0 1.0 null 75000 - 99999 0 0 1 3 1359.389277 163.0 40.222 32.950871 -96.683221 1 87500.0 1.0 15.0 Married 100000 - 124999 1 0 1 2 571.231533 235.0 82.387 33.143345 -96.770178 3 70000.0 0.0 6.0 Married 175000 - 199999 1 1 1 2 1439.698393 5332.0 44.474 33.180583 -96.917024 3 87500.0 1.0 9.0 Married 100000 - 124999 1 1 1 2 705.461263 5095.0 39.387 null null 3 47500.0 1.0 2.0 Married 175000 - 199999 0 0 1 2 1239.998157 106.0 47.053 32.948199 -96.723273 1 62500.0 0.0 12.0 Single 1000 - 24999 1 0 1 1 343.993275 5230.0 89.558 32.672206 -97.158259 2 70000.0 0.0 15.0 Married 75000 - 99999 1 0 1 2 1225.955771 4308.0 44.14 32.999225 -97.068418 3 250000.0 0.0 8.0 Married 150000 - 174999 1 1 1 2 846.935188 3922.0 60.893 32.849723999999995 -96.96622 1 125000.0 0.0 15.0 Single 150000 - 174999 1 0 1 1 1201.134006 80.0 55.444 null null 1 12500.0 0.0 0.0 null null 0 0 1 3 1042.806697 129.0 53.306 32.66534 -96.916357 1 87500.0 1.0 5.0 Married 125000 - 149999 1 0 1 2 1061.290149 6291.0 58.387 32.333374 -96.66509 3 87500.0 1.0 2.0 Married 125000 - 149999 1 0 1 2 964.828338 116.0 33.807 33.171758 -96.698662 3 87500.0 0.0 4.0 Single 100000 - 124999 1 0 1 1 1134.149279 80.0 39.89 null null 3 87500.0 1.0 0.0 Married null 0 1 1 2 881.815219 337.0 64.14 32.849107 -97.388363 2 125000.0 0.0 10.0 Married 75000 - 99999 1 1 1 2 777.013338 118.0 50.305 32.643711 -97.026669 1 57500.0 0.0 1.0 Married 25000 - 49999 1 0 1 2 824.728469 198.0 72.055 32.704478 -97.316443 2 22500.0 0.0 5.0 Marr

In [ ]:
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType
def hm_enc(val):
    
    if val==None:
        return 0
    elif val=='1000000 Plus':
        return 1000000    
    else:
        l_comp=val.split('-')

        m=(int(l_comp[0])+int(l_comp[1]))/2

    return m

hm_udf = udf(hm_enc, StringType())

m2_df_transformed = m2_df.withColumn("hm_enc", hm_udf(m2_df["HOME_MARKET_VALUE"]))

In [ ]:
m2_df_transformed=m2_df_transformed.drop("HOME_MARKET_VALUE","MARITAL_STATUS")

# Model

In [ ]:
m2_df_pandas = m2_df_transformed.toPandas()

m2_df_pandas = m2_df_pandas.dropna()

tgt=m2_df_pandas['Churn']

features = m2_df_pandas.drop('Churn', axis=1)

In [ ]:
m2_df_pandas.shape

(194077, 14)

In [ ]:
import numpy as np
features = np.array(features, dtype=np.float32)
tgt = np.array(tgt, dtype=np.float32)

In [ ]:
import tensorflow as tf

train_size = 99367

test_size=38815

tgt = np.asarray(tgt).astype('float32')

m2_df_tflow = tf.data.Dataset.from_tensor_slices((features, tgt))

m2_df_tflow = m2_df_tflow.shuffle(buffer_size=100)

batch_size = 32

# Shuffle and batch the dataset
m2_df_tflow = m2_df_tflow.shuffle(buffer_size=len(m2_df_pandas)).batch(batch_size).prefetch(buffer_size=tf.data.AUTOTUNE)

train_dataset = m2_df_tflow.take(train_size)
test_dataset = m2_df_tflow.skip(train_size).take(test_size)

In [ ]:
import time
def train(batch_size):
    import numpy as np
    import tensorflow as tf
    from tensorflow.keras.models import Sequential
    from tensorflow.keras.layers import Dense, Flatten

def build_nn_model():
    model = Sequential([
    tf.keras.layers.Input(shape=(features.shape[1],)),  # Flatten the 28x28 input images into a 1D array
    Dense(32, activation='relu'),  # First hidden layer with 128 neurons, ReLU activation
    Dense(16, activation='relu'),   # Second hidden layer with 64 neurons, ReLU activation
    Dense(1, activation='sigmoid') # Output layer with 10 neurons for each class, softmax activation
])
    
    model.compile(
    optimizer='adam',
    loss= 'binary_crossentropy',  # Adjust the loss function based on the problem (e.g., BinaryCrossentropy for binary classification)
    metrics=['accuracy']  # Adjust metrics based on the problem
)
    
    return model

multi_worker_model = build_nn_model()

options = tf.data.Options()

options.experimental_distribute.auto_shard_policy = tf.data.experimental.AutoShardPolicy.DATA

train_dataset_1 = train_dataset.with_options(options)

test_dataset_1 = test_dataset.with_options(options)

start = time.time()

multi_worker_model.fit(x=train_dataset_1, epochs=3)

done = time.time()

elapsed=done-start

print(elapsed)


Epoch 1/3
3981/6065 ━━━━━━━━━━━━━━━━━━━━ 3s 2ms/step - accuracy: 1.0000 - los

*** WARNING: max output size exceeded, skipping output. ***

6065/6065 ━━━━━━━━━━━━━━━━━━━━ 11s 2ms/step - accuracy: 1.0000 - loss: 0.0000e+00
32.40069651603699


---------------------------------------------------------------------------
ValueError                                Traceback (most recent call last)
File <command-3829152574602933>, line 44
     40 elapsed=done-start
     42 print(elapsed)
---> 44 multi_worker_model.evaluate(x=train_dataset_1, epochs=3)

File /local_disk0/.ephemeral_nfs/envs/pythonEnv-8c987702-9e30-4170-a8f0-142bd064f2f2/lib/python3.10/site-packages/keras/src/utils/traceback_utils.py:122, in filter_traceback.<locals>.error_handler(*args, **kwargs)
    119     filtered_tb = _process_traceback_frames(e.__traceback__)
    120     # To get the full stack trace, call:
    121     # `keras.config.disable_traceback_filtering()`
--> 122     raise e.with_traceback(filtered_tb) from None
    123 finally:
    124     del filtered_tb

File /local_disk0/.ephemeral_nfs/envs/pythonEnv-8c987702-9e30-4170-a8f0-142bd064f2f2/lib/python3.10/site-packages/keras/src/backend/tensorflow/trainer.py:392, in TensorFlowTrainer.evaluate(self, x

In [ ]:
import mlflow
import mlflow.tensorflow

with mlflow.start_run(): 

    mlflow.log_params(params)

    with strategy.scope():

        multi_worker_model = build_nn_model()

        options = tf.data.Options()

        options.experimental_distribute.auto_shard_policy = tf.data.experimental.AutoShardPolicy.DATA

        train_dataset_1 = train_dataset.with_options(options)

        test_dataset_1 = test_dataset.with_options(options)

        start = time.time()

        multi_worker_model.fit(x=train_dataset_1, epochs=3)

        done = time.time()

        elapsed=done-start

        print(elapsed)
        
        model.fit(train_dataset, epochs=2)

        # Log the entire model
        mlflow.tensorflow.log_model(model, 'model')

Epoch 1/3


2024-07-03 00:37:52.966277: W tensorflow/core/framework/dataset.cc:959] Input of GeneratorDatasetOp::Dataset will not be optimized because the dataset does not implement the AsGraphDefInternal() method needed to apply optimizations.


3057/6065 ━━━━━━━━━━━━━━━━━━━━ 6s 2ms/step - accuracy: 0.9994 - l

*** WARNING: max output size exceeded, skipping output. ***

6065/6065 ━━━━━━━━━━━━━━━━━━━━ 16s 2ms/step - accuracy: 0.9997 - loss: 0.4597
Epoch 2/3


2024-07-03 00:38:08.461531: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node MultiDeviceIteratorGetNextFromShard}}]]




*** WARNING: max output size exceeded, skipping output. ***

6065/6065 ━━━━━━━━━━━━━━━━━━━━ 21s 2ms/step - accuracy: 1.0000 - loss: 8.3963e-21
Epoch 3/3


...

2024-07-03 00:38:43.490037: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node MultiDeviceIteratorGetNextFromShard}}]]


2914/6065 ━━━━━━━━━━━━━━━━━━━━ 7s 2ms/step - accuracy: 1.0000 - loss: 0.0000e+00

*** WARNING: max output size exceeded, skipping output. ***

6065/6065 ━━━━━━━━━━━━━━━━━━━━ 15s 2ms/step - accuracy: 1.0000 - loss: 0.0000e+00
Epoch 2/2


2024-07-03 00:38:58.197469: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node MultiDeviceIteratorGetNextFromShard}}]]


2970/

*** WARNING: max output size exceeded, skipping output. ***

6065/6065 ━━━━━━━━━━━━━━━━━━━━ 14s 2ms/step - accuracy: 1.0000 - loss: 0.0000e+00


2024-07-03 00:39:12.334280: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
	 [[{{node MultiDeviceIteratorGetNextFromShard}}]]
2024/07/03 00:39:12 WARNING mlflow.tensorflow: You are saving a TensorFlow Core model or Keras model without a signature. Inference with mlflow.pyfunc.spark_udf() will not work unless the model's pyfunc representation accepts pandas DataFrames as inference inputs.
/databricks/python/lib/python3.10/site-packages/_distutils_hack/__init__.py:33: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")
2024/07/03 00:39:20 WARNING mlflow.models.model: Model logged without a signature. Signatures will be required for upcoming model registry features as they validate model inputs and denote the expected schema of model outputs. Please visit https://www.mlflow.org/docs/2.14.1/models.html#set-signature-on-logged-model for instructions on setting a mo